# Credit Risk Pipeline Quickstart

This notebook runs the **Unified Risk Pipeline** end-to-end on the bundled synthetic dataset.
The sample includes stratified monthly observations, calibration hold-outs, stage-2 data, and a future scoring batch
so each major step can be validated quickly.


## 0. Environment setup

This cell ensures `risk-pipeline` 0.4.1 is installed from the GitHub `development` branch.
Restart the kernel and rerun after refreshing the environment.


In [4]:
import importlib
import importlib.metadata as metadata
import subprocess
import sys

TARGET_VERSION = "0.4.1"
GIT_SPEC = "risk-pipeline[ml,notebook] @ git+https://github.com/selimoksuz/risk-model-pipeline.git@development"
PREREQ_PACKAGES = [
    "numba==0.59.1",
    "llvmlite==0.42.0",
    "scipy==1.11.4",
    "pandas==2.3.2",
    "tsfresh==0.20.1",
    "matrixprofile==1.1.10",
    "shap==0.48.0",
    "stumpy==1.13.0",
]

def _parse_version(value: str):
    parts = []
    for part in value.split('.'):
        if not part.isdigit():
            break
        parts.append(int(part))
    return tuple(parts)

def _run_pip(args):
    subprocess.check_call([
        sys.executable,
        "-m",
        "pip",
        "install",
        "--no-cache-dir",
        "--upgrade",
        "--force-reinstall",
        *args,
    ])

def _install_prerequisites():
    print(f"Installing prerequisite stack: {', '.join(PREREQ_PACKAGES)}")
    _run_pip(PREREQ_PACKAGES)

def _sanity_check():
    import shap  # noqa: F401
    from llvmlite import binding as _ll_binding
    _ = _ll_binding.ffi.lib
    from numba import njit

    @njit
    def _probe(x):
        return x + 1

    assert _probe(1) == 2

def _tsfresh_smoke_test():
    import pandas as pd
    from tsfresh import extract_features
    from tsfresh.feature_extraction import EfficientFCParameters

    data = pd.DataFrame(
        {
            "id": ["a", "a", "a", "b", "b", "b"],
            "time": [0, 1, 2, 0, 1, 2],
            "value": [1.0, 2.0, 3.0, 4.0, 9.0, 16.0],
        }
    )
    features = extract_features(
        data,
        column_id="id",
        column_sort="time",
        column_value="value",
        default_fc_parameters=EfficientFCParameters(),
        disable_progressbar=True,
        n_jobs=0,
    )
    if not any("entropy" in col for col in features.columns):
        raise RuntimeError("tsfresh smoke test did not produce entropy features")

def ensure_risk_pipeline():
    try:
        importlib.import_module("risk_pipeline")
        installed = metadata.version("risk-pipeline")
        if _parse_version(installed) < _parse_version(TARGET_VERSION):
            raise ModuleNotFoundError(f"risk-pipeline {installed} < {TARGET_VERSION}")
        print(f"risk-pipeline {installed} already installed.")
        _sanity_check()
        _tsfresh_smoke_test()
    except Exception as exc:
        print(f"risk-pipeline import failed: {exc}")
        try:
            _install_prerequisites()
            print(f"Attempting GitHub install: {GIT_SPEC}")
            _run_pip([GIT_SPEC])
            print("GitHub install succeeded.")
            raise SystemExit("Installation complete. Restart the kernel and rerun this cell.")
        except subprocess.CalledProcessError as err:
            print(f"GitHub install failed: {err}")
            raise SystemExit("Installation failed. Review the errors above.")
    else:
        print("Numba/llvmlite sanity check passed.")
        print("tsfresh smoke test passed (entropy features available).")

ensure_risk_pipeline()


risk-pipeline import failed: unexpected indent (data_processor.py, line 254)
Installing prerequisite stack: numba==0.59.1, llvmlite==0.42.0, scipy==1.11.4, pandas==2.3.2, tsfresh==0.20.1, matrixprofile==1.1.10, shap==0.48.0, stumpy==1.13.0
GitHub install failed: Command '['c:\\Users\\Acer\\anaconda3\\envs\\risk-pipeline-3\\python.exe', '-m', 'pip', 'install', '--no-cache-dir', '--upgrade', '--force-reinstall', 'numba==0.59.1', 'llvmlite==0.42.0', 'scipy==1.11.4', 'pandas==2.3.2', 'tsfresh==0.20.1', 'matrixprofile==1.1.10', 'shap==0.48.0', 'stumpy==1.13.0']' returned non-zero exit status 1.


SystemExit: Installation failed. Review the errors above.

c:\Users\Acer\anaconda3\envs\risk-pipeline-3\lib\site-packages\IPython\core\interactiveshell.py:3587: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


## 1. Imports and sample loader

The dataset ships with the package under `risk_pipeline.data.sample`.

In [3]:
from pathlib import Path
import pandas as pd

from IPython.display import display

from risk_pipeline.core.config import Config
from risk_pipeline.unified_pipeline import UnifiedRiskPipeline
from risk_pipeline.data.sample import load_credit_risk_sample

sample = load_credit_risk_sample()
OUTPUT_DIR = Path('output/credit_risk_sample_notebook')
OUTPUT_DIR.mkdir(parents=True, exist_ok=True)

dev_df = sample.development
cal_long_df = sample.calibration_longrun
cal_recent_df = sample.calibration_recent
score_df = sample.scoring_future
data_dictionary = sample.data_dictionary

dev_df.head()

IndentationError: unexpected indent (data_processor.py, line 254)

## 2. Quick sanity checks

In [ ]:
dev_df['target'].value_counts(normalize=True).rename('default_rate')

target
0    0.72018
1    0.27982
Name: default_rate, dtype: float64

In [2]:
dev_df.groupby('snapshot_month')['target'].mean().rename('monthly_default_rate')

NameError: name 'dev_df' is not defined

## 3. Configure the pipeline

The configuration below enables dual modelling (raw + WoE), Optuna (single rapid trial), balanced model selection with stability guard rails,
noise sentinel monitoring, SHAP explainability, the WoE-LI and Shao logistic challengers, and the PD-constrained risk band optimizer.
Train/Test/OOT ratios and all threshold knobs (PSI/IV/Gini/Correlation) are explicit so the notebook mirrors production-ready configuration files.

In [23]:
cfg = Config(
    target_column='target',
    id_column='customer_id',
    time_column='app_dt',
    create_test_split=True,
    use_test_split=True,
    train_ratio=0.6,
    test_ratio=0.2,
    oot_ratio=0.2,
    stratify_test=True,
    oot_months=2,
    enable_dual=True,
    enable_tsfresh_features=True,
    tsfresh_feature_set='efficient',
    tsfresh_n_jobs=-1,
    enable_scoring=True,
    enable_stage2_calibration=True,
    stage2_target_rate=0.11,
    output_folder=str(OUTPUT_DIR),
    selection_steps=['psi', 'univariate', 'iv', 'correlation', 'boruta', 'stepwise'],
    algorithms=[
        'logistic', 'gam', 'catboost', 'lightgbm', 'xgboost',
        'randomforest', 'extratrees', 'woe_boost', 'woe_li', 'shao', 'xbooster',
    ],
    model_selection_method='balanced',
    model_stability_weight=0.25,
    min_gini_threshold=0.45,
    max_train_oot_gap=0.08,
    psi_threshold=0.25,
    iv_threshold=0.02,
    univariate_gini_threshold=0.05,
    correlation_threshold=0.95,
    vif_threshold=5.0,
    woe_binning_strategy='iv_optimal',
    use_optuna=True,
    n_trials=1,
    optuna_timeout=120,
    hpo_method='optuna',
    hpo_trials=1,
    hpo_timeout_sec=120,
    use_noise_sentinel=True,
    calculate_shap=True,
    shap_sample_size=500,
    risk_band_method='pd_constraints',
    n_risk_bands=8,
    risk_band_min_bins=7,
    risk_band_max_bins=10,
    risk_band_micro_bins=1000,
    risk_band_min_weight=0.05,
    risk_band_max_weight=0.30,
    risk_band_hhi_threshold=0.15,
    risk_band_binomial_pass_weight=0.85,
    risk_band_alpha=0.05,
    risk_band_pd_dr_tolerance=1e-4,
    risk_band_max_iterations=100,
    risk_band_max_phase_iterations=50,
    risk_band_early_stop_rounds=10,
    calibration_stage1_method='isotonic',
    calibration_stage2_method='lower_mean',
    random_state=42,
)
cfg.model_type = 'all'


TypeError: Config.__init__() got an unexpected keyword argument 'stage2_target_rate'

## 4. Run the unified pipeline

In [24]:
pipe = UnifiedRiskPipeline(cfg)
results = pipe.fit(
    dev_df,
    data_dictionary=data_dictionary,
    calibration_df=cal_long_df,
    stage2_df=cal_recent_df,
    score_df=score_df,
)

UNIFIED RISK PIPELINE EXECUTION

[Step 1/10] Data Processing...
  Added 7830 tsfresh features
  Found 7840 numeric and 5 categorical features

[Step 2/10] Data Splitting...
  train: 14924 samples, default rate: 28.00%
  test: 3738 samples, default rate: 27.90%
  oot: 5332 samples, default rate: 27.98%

[DUAL] Running RAW and WOE flows and selecting the best by AUC...

[Step 3/10] WOE Transformation & Univariate Analysis...
  WOE hesaplandi: 7846 degisken

[Step 4/10] Feature Selection...
  Applying psi selection...
    Removing channel_code: oot psi 0.303 > 0.250
    Removing promo_flag: oot psi 0.463 > 0.250
    psi: 2 degisken cikarildi, 7844 kaldi
  Applying univariate selection...
    Removing app_id: univariate gini 0.000 < 0.050
    Removing open_trades: univariate gini 0.010 < 0.050
    Removing noise_feature: univariate gini 0.019 < 0.050
    Removing balance_to_limit__variance_larger_than_standard_deviation_tsfresh: univariate gini 0.000 < 0.050
    Removing balance_to_limit__

[I 2025-09-28 12:16:44,164] A new study created in memory with name: no-name-70c90ca1-26b7-4add-86ae-352619508620


      Train AUC: 0.9084, OOT AUC: 0.8845, Test AUC: 0.9099, |Train-OOT Gini gap|: 0.0478
    Training RandomForest...


[I 2025-09-28 12:16:46,533] Trial 0 finished with value: 0.9560437371148233 and parameters: {'n_estimators': 144, 'max_depth': 10, 'min_samples_split': 40, 'min_samples_leaf': 14}. Best is trial 0 with value: 0.9560437371148233.
[I 2025-09-28 12:16:49,806] A new study created in memory with name: no-name-7578f2d5-3db2-4692-9e18-c831aa2aa9df


      Train AUC: 0.9691, OOT AUC: 0.9235, Test AUC: 0.9560, |Train-OOT Gini gap|: 0.0912
    Training ExtraTrees...


...

      Train AUC: 0.9991, OOT AUC: 0.9440, Test AUC: 0.9791, |Train-OOT Gini gap|: 0.1102
    Training XBooster...


[I 2025-09-28 13:18:48,299] A new study created in memory with name: no-name-c9327197-5aa1-4f99-9fe2-817f8edba3ee


      Train AUC: 0.9777, OOT AUC: 0.9445, Test AUC: 0.9751, |Train-OOT Gini gap|: 0.0664
    Training GAM...


[I 2025-09-28 13:18:57,783] Trial 0 finished with value: 0.9748246548684845 and parameters: {'n_splines': 12, 'lam': 6.351221010640703}. Best is trial 0 with value: 0.9748246548684845.


      Train AUC: 0.9760, OOT AUC: 0.9456, Test AUC: 0.9748, |Train-OOT Gini gap|: 0.0609
    Training WoeBoost...
      Train AUC: 0.9897, OOT AUC: 0.9491, Test AUC: 0.9807, |Train-OOT Gini gap|: 0.0812
    Training WoeLogisticInteraction...
      Train AUC: 0.9729, OOT AUC: 0.9433, Test AUC: 0.9723, |Train-OOT Gini gap|: 0.0593
    Training ShaoLogit...
      Train AUC: 0.9721, OOT AUC: 0.9424, Test AUC: 0.9712, |Train-OOT Gini gap|: 0.0594
    Best model: GAM (OOT AUC: 0.9456, method: balanced), |train-oot gini gap|: 0.0609

[Step 6/10] Stage 1 Calibration...
  Added 7830 tsfresh features
  Found 7840 numeric and 5 categorical features
    Applying Stage 1 calibration (method=isotonic)...
      Stage 1 target (long-run mean) default rate: 26.02%
      ECE: 0.0000
      MCE: 0.0000
      Brier Score: 0.1925

[Step 7/10] Stage 2 Calibration...
  Added 7830 tsfresh features
  Found 7840 numeric and 5 categorical features
    Applying Stage 2 calibration (method=lower_mean)...
      Rece


## 5. Inspect key outputs

In [25]:
best_model = results.get('best_model_name')
model_scores = results.get('model_results', {}).get('scores', {})
print(f'Best model: {best_model}')
pd.DataFrame(model_scores).T

Best model: GAM


train_auc  test_auc   oot_auc  train_gini  test_gini  \
LogisticRegression       0.972120  0.971179  0.942459    0.944240   0.942358   
RandomForest             0.974484  0.968969  0.936756    0.948968   0.937938   
ExtraTrees               0.966710  0.963031  0.932185    0.933421   0.926061   
LightGBM                 0.998746  0.977951  0.945344    0.997492   0.955903   
XGBoost                  0.995709  0.979851  0.947403    0.991417   0.959702   
CatBoost                 0.999095  0.979065  0.943987    0.998189   0.958131   
XBooster                 0.977744  0.975124  0.944540    0.955489   0.950247   
GAM                      0.976038  0.974825  0.945566    0.952075   0.949649   
WoeBoost                 0.989705  0.980698  0.949095    0.979409   0.961396   
WoeLogisticInteraction   0.972929  0.972346  0.943257    0.945858   0.944691   
ShaoLogit                0.972128  0.971192  0.942448    0.944255   0.942384   

                        oot_gini  train_oot_gap  
LogisticRegression      0.884917       0.059323  
RandomForest            0.873512       0.075456  
ExtraTrees              0.864371       0.069050  
LightGBM                0.890688       0.106804  
XGBoost                 0.894806       0.096611  
CatBoost                0.887974       0.110216  
XBooster                0.889079       0.066409  
GAM                     0.891131       0.060944  
WoeBoost                0.898191       0.081219  
WoeLogisticInteraction  0.886514       0.059344  
ShaoLogit               0.884896       0.059360

In [26]:
feature_report = pipe.reporter.reports_.get('features')
feature_report.head() if feature_report is not None else 'No feature report available.'

feature  \
0              bureau_score__quantile__q_0_7_tsfresh   
1  bureau_score__cwt_coefficients__coeff_11__w_20...   
2  bureau_score__cwt_coefficients__coeff_4__w_2__...   
3  bureau_score__cwt_coefficients__coeff_5__w_5__...   
4  bureau_score__cwt_coefficients__coeff_6__w_5__...   

                                         raw_feature description category  \
0              bureau_score__quantile__q_0_7_tsfresh                        
1  bureau_score__cwt_coefficients__coeff_11__w_20...                        
2  bureau_score__cwt_coefficients__coeff_4__w_2__...                        
3  bureau_score__cwt_coefficients__coeff_5__w_5__...                        
4  bureau_score__cwt_coefficients__coeff_6__w_5__...                        

         iv  gini_raw  gini_woe  gini_drop  is_tsfresh tsfresh_source  ...  \
0  1.796739 -0.636084  0.628685  -1.264769        True   bureau_score  ...   
1  1.601831 -0.613943  0.612627  -1.226570        True   bureau_score  ...   
2  1.554144 -0.605796  0.601024  -1.206821        True   bureau_score  ...   
3  1.345468 -0.598251  0.531173  -1.129424        True   bureau_score  ...   
4  1.067450 -0.535674  0.498395  -1.034069        True   bureau_score  ...   

  importance_RandomForest importance_ExtraTrees importance_LightGBM  \
0                0.170568              0.113933                 582   
1                0.112208              0.077502                 593   
2                0.071820              0.089750                 521   
3                0.062647              0.099591                 278   
4                0.042162              0.045809                 272   

   importance_XGBoost  importance_CatBoost  importance_XBooster  \
0            0.120637             6.153203             0.099489   
1            0.060546             6.728023             0.110056   
2            0.020383             4.444543             0.035074   
3            0.022873             2.733015             0.053041   
4            0.012994             2.319906             0.021727   

  importance_GAM  importance_WoeBoost  importance_WoeLogisticInteraction  \
0       0.033333         20505.263763                           0.033333   
1       0.033333          6651.807181                           0.033333   
2       0.033333          2001.101730                           0.033333   
3       0.033333          2198.152710                           0.033333   
4       0.033333           591.441450                           0.033333   

   importance_ShaoLogit  
0              0.033333  
1              0.033333  
2              0.033333  
3              0.033333  
4              0.033333  

[5 rows x 28 columns]

In [27]:
calibration_report = pipe.reporter.reports_.get('calibration')
calibration_report

{'stage1': {'method': 'isotonic',
  'metrics': {'ece': 1.1102230246251565e-16,
   'mce': 1.1102230246251565e-16,
   'brier': 0.19250077268809684,
   'log_loss': 0.5732764925198244,
   'mean_predicted': 0.2602100350058344,
   'mean_actual': 0.2602100350058343,
   'calibration_gap': 1.1102230246251565e-16},
  'details': {'method': 'isotonic',
   'long_run_rate': 0.2602100350058343,
   'base_rate': 0.2602100350058343}},
 'stage2': {'method': 'lower_mean',
  'metrics': {'ece': 5.551115123125783e-17,
   'mce': 5.551115123125783e-17,
   'brier': 0.22439999999999996,
   'log_loss': 0.6410354778811556,
   'mean_predicted': 0.33999999999999997,
   'mean_actual': 0.34,
   'calibration_gap': 5.551115123125783e-17},
  'details': {'method': 'lower_mean',
   'recent_rate': 0.34,
   'stage1_rate': 0.26021003500583434,
   'target_rate': 0.34,
   'adjustment_factor': 1.3066367713004483,
   'achieved_rate': 0.33999999999999997}}}

In [28]:
risk_band_source = pipe.results_.get('risk_bands')
risk_bands_table = pipe.reporter.generate_risk_band_report(risk_band_source) if risk_band_source else None
risk_bands_summary = pipe.reporter.reports_.get('risk_bands_summary_table')
risk_bands_tests = pipe.reporter.reports_.get('risk_bands_tests')

# Core tables
if isinstance(risk_bands_table, pd.DataFrame) and not risk_bands_table.empty:
    display(risk_bands_table)
else:
    display('No risk band table available.')

if isinstance(risk_bands_summary, pd.DataFrame) and not risk_bands_summary.empty:
    display(risk_bands_summary)
else:
    display('No risk band summary available.')

# Detailed binomial diagnostics akin to scoring notebook
if isinstance(risk_bands_tests, pd.DataFrame) and not risk_bands_tests.empty:
    preferred_columns = [
        'band',
        'band_label',
        'bin_range',
        'count',
        'weight_pct',
        'mean_pd',
        'observed_dr',
        'dr_pd_diff',
        'ci_lower_observed',
        'ci_upper_observed',
        'binomial_p_value',
        'binomial_result',
        'predicted_within_ci',
        'binomial_distance',
        'hhi_contrib',
        'ks',
    ]
    available_columns = [col for col in preferred_columns if col in risk_bands_tests.columns]
    binomial_view = risk_bands_tests[available_columns].rename(columns={
        'band_label': 'Band Label',
        'bin_range': 'Score Range',
        'count': 'Count',
        'weight_pct': 'Weight',
        'mean_pd': 'Mean PD',
        'observed_dr': 'Observed DR',
        'dr_pd_diff': 'DR Minus PD',
        'ci_lower_observed': 'CI Lower',
        'ci_upper_observed': 'CI Upper',
        'binomial_p_value': 'P-Value',
        'binomial_result': 'Binomial Result',
        'predicted_within_ci': 'PD Within CI',
        'binomial_distance': 'Absolute Gap',
        'hhi_contrib': 'HHI Contribution',
        'ks': 'KS',
    })
    display(binomial_view)
else:
    display('No binomial test results available.')


'No risk band table available.'

summary
0         Herfindahl Index: 0.0000
1                  Entropy: 0.0000
2         Gini Coefficient: 0.0000
3  Hosmer-Lemeshow p-value: 0.0000
4                KS Statistic: nan

'No binomial test results available.'

In [ ]:
scoring_output = results.get('scoring_output', {})
scored_df = scoring_output.get('dataframe')
scoring_metrics = scoring_output.get('metrics', {})

if isinstance(scored_df, pd.DataFrame) and not scored_df.empty:
    columns_to_show = ['customer_id', 'risk_score', 'risk_band']
    if cfg.target_column in scored_df.columns:
        columns_to_show.append(cfg.target_column)
    available_cols = [col for col in columns_to_show if col in scored_df.columns]
    print('Scored sample:')
    display(scored_df[available_cols].head())
else:
    print('No scored dataframe available.')

if isinstance(scoring_metrics, dict) and scoring_metrics:
    metrics_view = {
        'n_total': scoring_metrics.get('n_total'),
        'n_with_target': scoring_metrics.get('n_with_target'),
        'n_without_target': scoring_metrics.get('n_without_target'),
        'psi_score': scoring_metrics.get('psi_score'),
    }
    print('Scoring metrics overview:')
    display(pd.DataFrame([metrics_view]))
else:
    print('No scoring metrics available.')


## 6. Generated files

In [ ]:
sorted(p.relative_to(OUTPUT_DIR.parent) for p in OUTPUT_DIR.glob('**/*') if p.is_file())

## 7. XBooster scorecard

In [ ]:
xbooster_artifacts = results.get('model_results', {}).get('interpretability', {}).get('XBooster', {})
if isinstance(xbooster_artifacts, dict):
    scorecard_df = xbooster_artifacts.get('scorecard_points')
    warnings = xbooster_artifacts.get('warnings')
    display_obj = scorecard_df.head() if hasattr(scorecard_df, 'head') else xbooster_artifacts
else:
    warnings = None
    display_obj = 'No XBooster artifacts available.'
print('Warnings:', warnings if warnings else 'None')
display_obj

## 8. Automating via script

`examples/quickstart_demo.py` mirrors the steps above so the flow can be validated headless
(e.g. in CI pipelines).